<a href="https://colab.research.google.com/github/ziwon/learning-cuda/blob/main/ch04/ch04.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install git+https://github.com/andreinechaev/nvcc4jupyter.git

  Cloning https://github.com/andreinechaev/nvcc4jupyter.git to /tmp/pip-req-build-pswjg5cc
  Running command git clone --filter=blob:none --quiet https://github.com/andreinechaev/nvcc4jupyter.git /tmp/pip-req-build-pswjg5cc
  Resolved https://github.com/andreinechaev/nvcc4jupyter.git to commit 781ff5b76ba6c4c2d80dcbbec9983e147613cc71
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for nvcc4jupyter: filename=nvcc4jupyter-1.1.0-py3-none-any.whl size=8011 sha256=e2b2acbb79d726227ace2ffdeb18b901e4debb9cf9419b13a35a389a655ee4ac
  Stored in directory: /tmp/pip-ephem-wheel-cache-w3wtmtnf/wheels/a8/b9/18/23f8ef71ceb0f63297dd1903aedd067e6243a68ea756d6feea
Successfully built nvcc4jupyter


In [2]:
%load_ext nvcc4jupyter

Source files will be saved in "/tmp/tmpf_8e3hng".


In [3]:
from IPython.core.magic import register_cell_magic
import subprocess
import shlex
import os

@register_cell_magic
def cu(line: str, cell: str) -> None:
    """Jupyter Notebook cell magic to run CUDA C code."""

    source_file_name = 'temp.cu'
    executable_name = 'temp.out'

    with open(source_file_name, 'w') as f:
        f.write(cell)

    compile_command = f"nvcc {source_file_name} -o {executable_name}"
    subprocess.run(shlex.split(compile_command), check=True)

    run_command = f"./{executable_name}"
    result = subprocess.run(shlex.split(run_command), text=True, capture_output=True)
    print(result.stdout)

    os.remove(source_file_name)
    os.remove(executable_name)

In [8]:
%%cu

#include "cuda_runtime.h"
#include "device_launch_parameters.h"

#include <stdio.h>
#include <stdlib.h>
#include <string.h>

__global__ void checkIndex(void) {
    printf("threadIdx:(%d, %d, %d) blockIdx:(%d, %d, %d) blockDim:(%d, %d, %d) gridDim:(%d, %d, %d)\n"
           , threadIdx.x, threadIdx.y, threadIdx.z
           , blockIdx.x, blockIdx.y, blockIdx.z
           , blockDim.x, blockDim.y, blockDim.z
           , gridDim.x, gridDim.y, gridDim.z);
}

int main(void)
{
    dim3 dimBlock(3,1,1); // or dimBlock(3)
    dim3 dimGrid(2,1,1); // or dimGrid(2)

    printf("dimGrid.x=%d dimGrid.y=%d dimGrid.z=%d\n", dimGrid.x, dimGrid.y, dimGrid.z);
    printf("dimBlock.x=%d dimBlock.y=%d dimBlock.z=%d\n", dimBlock.x, dimBlock.y, dimBlock.z);

    checkIndex<<<dimGrid, dimBlock>>>();

    return 0;
}

dimGrid.x=2 dimGrid.y=1 dimGrid.z=1
dimBlock.x=3 dimBlock.y=1 dimBlock.z=1



In [10]:
%%cu
#include <stdio.h>
#include <stdlib.h>
#include <string.h>

__global__ void addOne(int *a, int N) {
    int threadId = blockIdx.x * blockDim.x + threadIdx.x;
    if (threadId < N) {
        a[threadId] += 1;
    }
}

int main() {
    const int N = 1024; // 배열 크기
    int *a, *d_a; // 호스트 및 디바이스 포인터

    // 호스트 메모리 할당
    a = (int*)malloc(N * sizeof(int));

    // 초기 데이터 준비
    for(int i = 0; i < N; i++) {
        a[i] = i;
    }

    // 디바이스 메모리 할당
    cudaMalloc(&d_a, N * sizeof(int));

    // 호스트에서 디바이스로 데이터 복사
    cudaMemcpy(d_a, a, N * sizeof(int), cudaMemcpyHostToDevice);

    // 그리드와 블록의 차원 설정
    int blockSize = 256; // 블록당 스레드 수
    int numBlocks = (N + blockSize - 1) / blockSize; // 필요한 블록 수

    // 커널 실행
    addOne<<<numBlocks, blockSize>>>(d_a, N);

    // 디바이스에서 호스트로 결과 복사
    cudaMemcpy(a, d_a, N * sizeof(int), cudaMemcpyDeviceToHost);

    // 결과 출력
    for(int i = 0; i < N; i++) {
        printf("%d ", a[i]);
    }
    printf("\n");

    // 메모리 해제
    free(a);
    cudaFree(d_a);

    return 0;
}

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 

In [15]:
%%cuda

#include "cuda_runtime.h"
#include "device_launch_parameters.h"

#include <stdio.h>
#include <stdlib.h>
#include <string.h>


#define WIDTH 1024
#define HEIGHT 1024

// CUDA 커널:
__global__ void matrixAdd(const int *a, const int *b, int *c, int width, int height) {
    int x = blockIdx.x * blockDim.x + threadIdx.x;
    int y = blockIdx.y * blockDim.y + threadIdx.y;

    if (x < width && y < height) {
        int idx = y * width + x;
        c[idx] = a[idx] + b[idx];
    }

    printf("threadIdx:(%d, %d, %d) blockIdx:(%d, %d, %d) blockDim:(%d, %d, %d) gridDim:(%d, %d, %d)\n"
           , threadIdx.x, threadIdx.y, threadIdx.z
           , blockIdx.x, blockIdx.y, blockIdx.z
           , blockDim.x, blockDim.y, blockDim.z
           , gridDim.x, gridDim.y, gridDim.z);
}

int main() {
    int *a, *b, *c; // 호스트 메모리 포인터
    int *d_a, *d_b, *d_c; // 디바이스 메모리 포인터
    int size = WIDTH * HEIGHT * sizeof(int);

    // 호스트 메모리 할당
    a = (int*)malloc(size);
    b = (int*)malloc(size);
    c = (int*)malloc(size);

    // 초기화
    for(int i = 0; i < WIDTH * HEIGHT; i++) {
        a[i] = i;
        b[i] = i;
    }

    // 디바이스 메모리 할당
    cudaMalloc(&d_a, size);
    cudaMalloc(&d_b, size);
    cudaMalloc(&d_c, size);

    // 호스트에서 디바이스로 데이터 복사
    cudaMemcpy(d_a, a, size, cudaMemcpyHostToDevice);
    cudaMemcpy(d_b, b, size, cudaMemcpyHostToDevice);

    // 그리드와 블록의 차원 설정
    dim3 threadsPerBlock(16, 16);
    dim3 numBlocks((WIDTH + threadsPerBlock.x - 1) / threadsPerBlock.x,
                   (HEIGHT + threadsPerBlock.y - 1) / threadsPerBlock.y);

    // 커널 실행
    matrixAdd<<<numBlocks, threadsPerBlock>>>(d_a, d_b, d_c, WIDTH, HEIGHT);

    // 디바이스에서 호스트로 결과 복사
    cudaMemcpy(c, d_c, size, cudaMemcpyDeviceToHost);

    // 결과 검증 (여기서는 첫 번째 요소만 출력)
    printf("c[0] = %d\n", c[0]);

    // 메모리 해제
    free(a);
    free(b);
    free(c);
    cudaFree(d_a);
    cudaFree(d_b);
    cudaFree(d_c);

    return 0;
}

Streaming output truncated to the last 5000 lines.
threadIdx:(15, 2, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(0, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(1, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(2, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(3, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(4, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(5, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(6, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(7, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(8, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(9, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(10, 3, 0) blockIdx:(22, 4, 0) blockDim:(16, 16

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
threadIdx:(1, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(2, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(3, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(4, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(5, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(6, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(7, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(8, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(9, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(10, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(11, 15, 0) blockIdx:(14, 11, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(12, 15, 0) blockIdx:(14

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
threadIdx:(13, 11, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(14, 11, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(15, 11, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(0, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(1, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(2, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(3, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(4, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(5, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(6, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(7, 6, 0) blockIdx:(8, 13, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(8, 6, 0) blockIdx:(8, 13, 0) blockDim:(16

...

Streaming output truncated to the last 5000 lines.
threadIdx:(14, 10, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(15, 10, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(0, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(1, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(2, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(3, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(4, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(5, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(6, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(7, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(8, 11, 0) blockIdx:(63, 57, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(9, 11, 0) blockIdx:(63,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
threadIdx:(0, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(1, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(2, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(3, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(4, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(5, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(6, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(7, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(8, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(9, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(10, 7, 0) blockIdx:(36, 61, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(11, 7, 0) blockIdx:(36, 61, 0) bloc

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
threadIdx:(10, 11, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(11, 11, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(12, 11, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(13, 11, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(14, 11, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(15, 11, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(0, 14, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(1, 14, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(2, 14, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(3, 14, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(4, 14, 0) blockIdx:(43, 63, 0) blockDim:(16, 16, 1) gridDim:(64, 64, 1)
threadIdx:(5, 14, 0) blockIdx: